# GOT

In [1]:
import time
from collections import namedtuple

import numpy as np
import tensorflow as tf

In [2]:
with open('gameofthrones.txt', 'r') as f:
    text = f.read()
vocab = set(text)
vocab_to_int = {c:i for i,c in enumerate(vocab)}
int_to_vocab = dict(enumerate(vocab))
encoded = np.array([vocab_to_int[c] for c in text], dtype= np.int32)

In [3]:
vocab

{'\n',
 ' ',
 '!',
 '(',
 ')',
 ',',
 '-',
 '.',
 '/',
 '0',
 '1',
 '2',
 '3',
 '4',
 '5',
 '6',
 '7',
 '8',
 '9',
 ':',
 ';',
 '?',
 'A',
 'B',
 'C',
 'D',
 'E',
 'F',
 'G',
 'H',
 'I',
 'J',
 'K',
 'L',
 'M',
 'N',
 'O',
 'P',
 'Q',
 'R',
 'S',
 'T',
 'U',
 'V',
 'W',
 'X',
 'Y',
 'Z',
 '[',
 ']',
 'a',
 'b',
 'c',
 'd',
 'e',
 'f',
 'g',
 'h',
 'i',
 'j',
 'k',
 'l',
 'm',
 'n',
 'o',
 'p',
 'q',
 'r',
 's',
 't',
 'u',
 'v',
 'w',
 'x',
 'y',
 'z',
 '{',
 '}',
 'é',
 'ê',
 '—',
 '‘',
 '’',
 '“',
 '”',
 '…'}

In [4]:
text[:100]

'\n\n“We should start back,” Gared urged as the woods began to grow dark around them. “The wildlings ar'

In [5]:
encoded[:100]

array([31, 31,  5, 79, 33, 18, 14, 47, 12, 58, 71, 65, 18, 14,  3, 35, 20,
        3, 18, 49, 35, 22, 60, 17, 41, 18, 13, 35, 20, 33, 65, 18, 58, 20,
       76, 33, 65, 18, 35, 14, 18,  3, 47, 33, 18, 75, 12, 12, 65, 14, 18,
       49, 33, 76, 35, 69, 18,  3, 12, 18, 76, 20, 12, 75, 18, 65, 35, 20,
       60, 18, 35, 20, 12, 58, 69, 65, 18,  3, 47, 33, 25, 11, 18,  5, 39,
       47, 33, 18, 75, 85, 71, 65, 71, 85, 69, 76, 14, 18, 35, 20], dtype=int32)

In [6]:
len(encoded)

5662324

Since the network is working with individual characters, it's similar to a classification problem in which we are trying to predict the next character from the previous text. Here's how many 'classes' our network has to pick from

In [7]:
len(vocab)

86

## Making Training Mini-Batches!

In [8]:
def get_batches(arr, n_seqs, n_steps):
    
    # Get number of characters per batch and number of batches we can make
    characters_per_batch = n_seqs * n_steps
    n_batches = len(arr)//characters_per_batch
    
    # Keep only enough characters to make full batches
    arr = arr[:characters_per_batch * n_batches]
    
    # Reshape into n_seqs rows
    arr = arr.reshape((n_seqs , -1))
    
    for n in range(0, arr.shape[1], n_steps):
        
        x = arr[: , n:n+n_steps]
        y = np.zeros_like(x)
        y[:,:-1] , y[:,-1] = x[: , 1:], x[:,0]
        yield x,y
    
    

In [9]:
batches = get_batches(encoded, n_seqs= 10, n_steps= 50)
x,y = next(batches)

In [10]:
print('x\n', x[:10, :10])

x
 [[31 31  5 79 33 18 14 47 12 58]
 [14 18  3 12 58 20 69 33 53 18]
 [14 18 49 33 14  3 18 25 33 69]
 [78 12 58 20 18 13 20 35 22 33]
 [18 35 14 18 35 18 76 12 58 20]
 [18 35 49 33 65 11 18 70 58  3]
 [47 33 18 25 85 76 47  3 18 69]
 [18 84 12 20 18 35 69 18 35 20]
 [35 69 53 11 18 39 47 33 18 84]
 [18 76 12 71 65 18 84 20 12 25]]


In [11]:
print('\ny\n', y[:10, :10])


y
 [[31  5 79 33 18 14 47 12 58 71]
 [18  3 12 58 20 69 33 53 18 75]
 [18 49 33 14  3 18 25 33 69 11]
 [12 58 20 18 13 20 35 22 33 11]
 [35 14 18 35 18 76 12 58 20 65]
 [35 49 33 65 11 18 70 58  3 18]
 [33 18 25 85 76 47  3 18 69 33]
 [84 12 20 18 35 69 18 35 20 22]
 [69 53 11 18 39 47 33 18 84 85]
 [76 12 71 65 18 84 20 12 25 18]]


In [12]:
x[:,0]

array([31, 14, 14, 78, 18, 18, 47, 18, 35, 18], dtype=int32)

In [13]:
y[:,-1]

array([31, 14, 14, 78, 18, 18, 47, 18, 35, 18], dtype=int32)

## Building the Model

##### Inputs

In [14]:
def build_inputs(batch_size, num_steps):
    
    # Declare placeholders we'll feed into the graph
    inputs = tf.placeholder(tf.int32, (batch_size , num_steps), name = 'inputs')
    targets = tf.placeholder(tf.int32, (batch_size, num_steps), name = 'targets')
    
    # Keep probability placeholder for dropout layers
    keep_prob = tf.placeholder(tf.float32)
    
    return inputs, targets, keep_prob

 ##### LSTM Cell

In [15]:
def build_lstm(lstm_size, num_layers, batch_size, keep_prob):
    
    # Build the LSTM Cell
    lstm = tf.contrib.rnn.BasicLSTMCell(lstm_size)
    
    #Add dropout to the cell outputs
    drop = tf.contrib.rnn.DropoutWrapper(lstm, output_keep_prob = keep_prob)
    
    #Stack up multiple LSTM layers, for deep learning
    cell = tf.contrib.rnn.MultiRNNCell([drop]*num_layers)
    initial_state = cell.zero_state(batch_size, tf.float32)
    
    return cell, initial_state   

##### RNN Output

In [16]:
def build_output(lstm_output, in_size, out_size):
    
    """
    lstm_output = NxMxL size output
    in_size     = size of LSTM cells
    out_size    = Size of the softmax layer

    """
    
    # Reshape output so it's a bunch of rows, one row for each step for each sequence
    # The shape should be batch_size * num_steps rows by lstm_size columns
    
    seq_output = tf.concat(lstm_output, axis = 1)
    x = tf.reshape(seq_output , [-1 , in_size])
    
    # Connect the RNN outputs to a softmax layer
    with tf.variable_scope('softmax'):
        softmax_w = tf.Variable(tf.truncated_normal((in_size, out_size), stddev=0.1))
        softmax_b = tf.Variable(tf.zeros(out_size))
        
        
    # Since outputs is a bunch of rows of RNN cell outputs, logits will be a bunch of rows of logit outputs,
    # one for each step and each sequence
    logits = tf.matmul(x , softmax_w) + softmax_b
    
    # Use softmax to get the probabilities of predicted characters
    out = tf.nn.softmax(logits , name = 'predictions')
    
    return logits, out        

##### Training Loss

In [17]:
def build_loss(logits, targets, lstm_size, num_classes):
    """
    Arguments
    ---------
        logits: Logits from final fully connected layer
        targets: Targets for supervised learning
        lstm_size: Number of LSTM hidden units
        num_classes: Number of classes in targets
        
    
    """
    
        
    # One-hot encode targets and reshape to match logits, one row per batch_size per step
    y_one_hot = tf.one_hot(targets, num_classes)
    y_reshaped = tf.reshape(y_one_hot, logits.get_shape())
    
    # Softmax cross entropy loss
    loss = tf.nn.softmax_cross_entropy_with_logits(logits = logits, labels = y_reshaped)
    loss = tf.reduce_mean(loss)
    return loss

##### Optimizer

In [18]:
def build_optimizer(loss, learning_rate, grad_clip):
    """
    Build optmizer for training, using gradient clipping.
    
        Arguments:
        loss: Network loss
        learning_rate: Learning rate for optimizer
    """
    
    # Optimizer for training, using gradient clipping to control exploding gradients
    tvars = tf.trainable_variables()
    grads, _ = tf.clip_by_global_norm(tf.gradients(loss, tvars), grad_clip)
    train_op = tf.train.AdamOptimizer(learning_rate)
    optimizer = train_op.apply_gradients(zip(grads,tvars))
    
    return optimizer

## Building the Network

In [19]:
class CharRNN:
    
    def __init__(self, num_classes, batch_size = 64, num_steps = 50, lstm_size = 128, num_layers = 2, learning_rate = 0.001,
                grad_clip = 5, sampling = False):
        
        # When we are using this model for sampling later, we'll be passing in one character at a time,
        # so providing an option for that
        
        if sampling == True:
            batch_size, num_steps = 1, 1
            
        else:
            batch_size, num_steps = batch_size, num_steps
            
        tf.reset_default_graph()
        
        # Build the input placeholder tensors
        self.inputs, self.targets, self.keep_prob = build_inputs(batch_size, num_steps)
        
        #Build the LSTM cell
        cell, self.initial_state = build_lstm(lstm_size, num_layers, batch_size, self.keep_prob)
        
        ### Run the data through RNN layers
        # First one-hot encode the input tokens
        x_one_hot = tf.one_hot(self.inputs, num_classes)
        
        # Run each sequence step through the RNN and collect the outputs
        outputs, state = tf.nn.dynamic_rnn(cell, x_one_hot , initial_state = self.initial_state)
        self.final_state = state
        
        # Get softmax predictions and logits
        self.logits, self.prediction = build_output(outputs, in_size = lstm_size, out_size= num_classes)
        
        # Loss and optimizer with gradient clipping
        self.loss = build_loss(self.logits, self.targets, lstm_size, num_classes)
        self.optimizer = build_optimizer(self.loss, learning_rate, grad_clip)
        

## Hyperparameters

In [20]:
batch_size = 50       # Sequences for batch
num_steps = 50        # Num of sequence steps per batch
lstm_size = 256        # Size of hidden layers in LSTM
num_layers = 2         # Number of LSTM layers
learning_rate = 0.001  # Learning rate
keep_prob = 0.6        # Dropout keep probability

## Time for Training

In [ ]:
epochs = 150
# Save every n iterations
save_every_n = 200

model = CharRNN(len(vocab), batch_size = batch_size, num_steps= num_steps, lstm_size= lstm_size, num_layers= num_layers,
               learning_rate = learning_rate)

saver = tf.train.Saver(max_to_keep=100)

with tf.Session() as sess:
    sess.run(tf.global_variables_initializer())
    
    # Use the line below to load a checkpoint and resume training
    # saver.restore(sess, 'checkpoints/______.ckpt')
    
    counter = 0
    for e in range(epochs):
        # Train Network
        new_state = sess.run(model.initial_state)
        loss = 0
        
        for x,y in get_batches(encoded, batch_size, num_steps):
            counter += 1
            start = time.time()
            feed = {model.inputs: x,
                    model.targets: y,
                    model.keep_prob: keep_prob,
                    model.initial_state: new_state}
            
            batch_loss , new_state, _ = sess.run([model.loss,
                                                  model.final_state,
                                                  model.optimizer],
                                                  feed_dict = feed)
            
            end = time.time()
            
            print('Epochs: {}/{}...'.format(e+1, epochs),
                  'Training Step: {}...'.format(counter),
                  'Training Loss: {:.4f}...'.format(batch_loss),
                  '{:.4f} sec/batch'.format((end-start)))
            
            if (counter % save_every_n == 0):
                saver.save(sess, "checkpoints/i{}_l{}.ckpt".format(counter, lstm_size))
                
    saver.save(sess, "checkpoints/i{}_l{}.ckpt".format(counter, lstm_size))
    
            
    
    

Epochs: 1/150... Training Step: 1... Training Loss: 4.4525... 1.9410 sec/batch
Epochs: 1/150... Training Step: 2... Training Loss: 4.4155... 0.1095 sec/batch
Epochs: 1/150... Training Step: 3... Training Loss: 4.3457... 0.1079 sec/batch
Epochs: 1/150... Training Step: 4... Training Loss: 4.1612... 0.0944 sec/batch
Epochs: 1/150... Training Step: 5... Training Loss: 3.6836... 0.0944 sec/batch
Epochs: 1/150... Training Step: 6... Training Loss: 3.6836... 0.0871 sec/batch
Epochs: 1/150... Training Step: 7... Training Loss: 3.5374... 0.0834 sec/batch
Epochs: 1/150... Training Step: 8... Training Loss: 3.4307... 0.0802 sec/batch
Epochs: 1/150... Training Step: 9... Training Loss: 3.4142... 0.0794 sec/batch
Epochs: 1/150... Training Step: 10... Training Loss: 3.3792... 0.0778 sec/batch
Epochs: 1/150... Training Step: 11... Training Loss: 3.3671... 0.0779 sec/batch
Epochs: 1/150... Training Step: 12... Training Loss: 3.3513... 0.0752 sec/batch
Epochs: 1/150... Training Step: 13... Training Lo

In [22]:
tf.train.get_checkpoint_state('checkpoints')

model_checkpoint_path: "checkpoints/i70600_l256.ckpt"
all_model_checkpoint_paths: "checkpoints/i50800_l256.ckpt"
all_model_checkpoint_paths: "checkpoints/i51000_l256.ckpt"
all_model_checkpoint_paths: "checkpoints/i51200_l256.ckpt"
all_model_checkpoint_paths: "checkpoints/i51400_l256.ckpt"
all_model_checkpoint_paths: "checkpoints/i51600_l256.ckpt"
all_model_checkpoint_paths: "checkpoints/i51800_l256.ckpt"
all_model_checkpoint_paths: "checkpoints/i52000_l256.ckpt"
all_model_checkpoint_paths: "checkpoints/i52200_l256.ckpt"
all_model_checkpoint_paths: "checkpoints/i52400_l256.ckpt"
all_model_checkpoint_paths: "checkpoints/i52600_l256.ckpt"
all_model_checkpoint_paths: "checkpoints/i52800_l256.ckpt"
all_model_checkpoint_paths: "checkpoints/i53000_l256.ckpt"
all_model_checkpoint_paths: "checkpoints/i53200_l256.ckpt"
all_model_checkpoint_paths: "checkpoints/i53400_l256.ckpt"
all_model_checkpoint_paths: "checkpoints/i53600_l256.ckpt"
all_model_checkpoint_paths: "checkpoints/i53800_l256.ckpt"
al

## Sampling

In [23]:
def pick_top_n(preds, vocab_size, top_n=5):
    p = np.squeeze(preds)
    p[np.argsort(p)[:-top_n]] = 0
    p = p / np.sum(p)
    c = np.random.choice(vocab_size, 1, p=p)[0]
    return c

In [24]:
def sample(checkpoint, n_samples, lstm_size, vocab_size, prime="The "):
    samples = [c for c in prime]
    model = CharRNN(len(vocab), lstm_size=lstm_size, sampling=True)
    saver = tf.train.Saver()
    with tf.Session() as sess:
        saver.restore(sess, checkpoint)
        new_state = sess.run(model.initial_state)
        for c in prime:
            x = np.zeros((1, 1))
            x[0,0] = vocab_to_int[c]
            feed = {model.inputs: x,
                    model.keep_prob: 1.,
                    model.initial_state: new_state}
            preds, new_state = sess.run([model.prediction, model.final_state], 
                                         feed_dict=feed)

        c = pick_top_n(preds, len(vocab))
        samples.append(int_to_vocab[c])

        for i in range(n_samples):
            x[0,0] = c
            feed = {model.inputs: x,
                    model.keep_prob: 1.,
                    model.initial_state: new_state}
            preds, new_state = sess.run([model.prediction, model.final_state], 
                                         feed_dict=feed)

            c = pick_top_n(preds, len(vocab))
            samples.append(int_to_vocab[c])
        
    return ''.join(samples)

In [25]:
tf.train.latest_checkpoint('checkpoints')

'checkpoints/i70600_l256.ckpt'

In [26]:
checkpoint = tf.train.latest_checkpoint('checkpoints')
samp = sample(checkpoint, 4000, lstm_size, len(vocab), prime="The")
print(samp)

Ther of the Sea, and the truth of them, bowels, and the stanning worse. Are you a little left?”

“True, the blood, they will too. A different more white, and then you can see her father. I’m a mouthful to sing it out. Any of the touch,” he said. “Which man was a long.”

“And woman, why.” He wet and carried the sharp tongres. “Your brother has the sea. And the cracks of the black sipped seven harrows, where is it was the book, but I have never been as step.” She was strong, the child behind their fiests. He wondered if when the sea of stand and shove him on stone.

That was her. The corpse would build three thick. Halfhall with the third septa and some the back of sheep would have claimed there were the same. She was not true, he held her hand, and his little sister was a ship over the courage.

The color when his half-brother told them to be the bannermen whose thought was a blow of blood, was hard to seat at once, and the chest of a boy. The trader ship, the crossbowmen will talk. The

In [28]:
# 2 
checkpoint = 'checkpoints/i53800_l256.ckpt'
samp = sample(checkpoint, 1000, lstm_size, len(vocab), prime="Far")
print(samp)

Farlen, an old man, so he drew the crunch. The wind was so blood, this is her brother of the Seven Kingdoms, and the worth of the sharpen of their sisters are sending his courage with her friend. A merchant was almost to stop their bloody all, they would never search the honored ship. It will never have heed our heirs. He could hope he had a brother that they stopped for him, and she will not have to be a beautiful time. It was short. He was not before. Her food in his company. He was back at him and the whole battle of the realm was a sickly of the castle born. He turned and called other horse trimmed and the steps were changed their horses and stable on his chest that crossed in the west. “Yee and made myself, a milk of your head to the sea, and I could have hidden the shortship that we could not have been better than I see, I saw a better silver,” so they were blind, half-a more too he could. Ser Jaime strode to such tenth, and with her brother he was there as well.

“And what would

In [29]:
checkpoint = 'checkpoints/i68400_l256.ckpt'
samp = sample(checkpoint, 1000, lstm_size, len(vocab), prime="Arya")
print(samp)

Arya said. He was night to the war of the sight of the way of the wheels, she heard standing with his solar, and another would believe him without the banners were. The walls of any tower thought, his stick, hard as and thicker than her son. “What if the man has brought his brother to see the wolves.”

The singer would say that, he was a strong, and the weight of his beard and a crossbow had to still be supposed to stay home to the chance of his battle, and that was his horse we had been a banner, but he had been been but that shadows, and how many shells hung at a shallow, all their sisters were a morth of strong brothers, so many and bent all her friend had to stop the wolf of a was honored bank of an angry she should have taken him.

“Your Grace,” Ser Rodrik asked. “It’s not.”

“A bank of when they will say it would never have been telling her of all the west as well.”

The song had taken the silver for her hair and began to beer. He talked about the wind when he had the chance. “I 

In [30]:
checkpoint = 'checkpoints/i70000_l256.ckpt'
samp = sample(checkpoint, 1000, lstm_size, len(vocab), prime="Sansa")
print(samp)

Sansa, he’d been sometimes as he had been a short. There was a battle of the south of hand. The wine was a stag as had he shouted. “We can. And why warness?”

Tyrion started at her, as it would be sunk.

“You do not know that you heard the bods to you this is seated toward his sisters and so though I was an angry to the way. He himself. The whole shoes is no more lies of her for the sight of the city. They’d been a single sigils of archer’s thinks, stiff, a boy of words and soldiers where you had never teres of sticks. The wind was always shouting, and some say this would be a fortnight, but it’s a lady man, they’ll have been a good stiff time to hang his sister’s cloak as they sent me too, though…”

“You have something.” She had not seen sharpening them as he shrinkled and down the clean old brothers. “The same, though. I want to show her all you’re the castle. The steel of more sharpsings says as which should be send to some more than I’m a steady.” That it was a good thing. “I hope 

In [31]:
checkpoint = 'checkpoints/i60000_l256.ckpt'
samp = sample(checkpoint, 1000, lstm_size, len(vocab), prime="John")
print(samp)

Johne Thorne, white and that serving silter horses would have saw its work of branches together and take.t Thoros was blunting out of his sword, he seemed to shoulder was worn, the bear of his head and the south are stepped onto the body, and a last horse had still have a look with their sword and the blind stones at the blink or shattering. He couldn’t charge it. His bed, he had always should be all the command of the three father of the Kingsguard, and the boy strong to heed in a black cloak that was true. They set aside and hus the wind they cannot below a single foot of her face and almost trying. “I will see this other,” Tyrion rosed black as his father, tree, to help. “Tell you to send your father’s friend?” Sansa told her staring. “As we might have a servant so shall.”

“Will they mean her sister, though you shall see your face?”

“Your lady work is a boy?”

“The boy has been still so brave a sterily a man.”

The stables of a book, her horse was safe and trickled at a hundred bl

In [32]:
checkpoint = tf.train.latest_checkpoint('checkpoints')
samp = sample(checkpoint, 3000, lstm_size, len(vocab), prime="Daenerys Targaryen")
print(samp)

Daenerys Targaryen and the retain talk of the walls and the camp, and his belly say he saw she could see it. That silver had been behind her, but he would not seem to do with her. The true sterrow set to she had, she’d been, and had been. The steps around and wise that a show, and and the word of the wolf shallowed, but to her. “Is it that you are too much?”

“It was the size of the window, some of the breath of the Wall.”r Highgarden saw her, hideen behind. He was bothing as he would not share the boy. Sansa was being bared. “Tell me a man who would not have them burn them, but I have been seen between the broken brown strangere and hust the world or hope.”

“Yes,” the gods said as her sword went on their stump. He saw a long well wish to be an apperance. “Why would they struck you to more take out and the bridge?”h

 the ships still said a long good servant stepping forward and spoke. “What do you want to be bloody?”

“You’re a men at orchands.” Sam could see the same bars. “The sort